<a href="https://colab.research.google.com/github/crisrib/hha507-AutoMLexamples/blob/main/AutoML_examples.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [3]:
import pandas as pd
import numpy as np

In [4]:
!pip install tpot mljar-supervised

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [5]:
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split
from supervised.automl import AutoML

In [6]:
import pandas as pd
sparcs = pd.read_csv('https://raw.githubusercontent.com/hantswilliams/HHA-507-2022/main/autoML/datasets/data_sparcs.csv')
sparcs

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Risk of Mortality APR Medical Surgical Description  \
0      ...                 Minor                          Medical   
1      ...                 Minor                          Medical   
2      ...                 Minor                          Medical   
3      ...              Moderate                          Medical   
4      ...                 Major                          Medical   
...    ...                   ...                              ...   
23578  ...              Moderate                          Medical   
23579  ...                 Minor                          Medical   
23580  ...                 Minor                          Medical   
23581  ...                 Major                          Medical   
23582  ...                 Major                          Medical   

             Payment Typology 1        Payment Typology 2  Payment Typology 3  \
0      Private Health Insurance                       NaN                 NaN   
1        Blue Cross/Blue Shield                  Self-Pay            Self-Pay   
2                      Self-Pay                  Self-Pay            Self-Pay   
3                      Medicare                  Medicare            Self-Pay   
4        Blue Cross/Blue Shield  

In [7]:
sparcs.columns

Index(['Health Service Area', 'Hospital County',
       'Operating Certificate Number', 'Facility Id', 'Facility Name',
       'Age Group', 'Zip Code - 3 digits', 'Gender', 'Race', 'Ethnicity',
       'Length of Stay', 'Type of Admission', 'Patient Disposition',
       'Discharge Year', 'CCS Diagnosis Code', 'CCS Diagnosis Description',
       'CCS Procedure Code', 'CCS Procedure Description', 'APR DRG Code',
       'APR DRG Description', 'APR MDC Code', 'APR MDC Description',
       'APR Severity of Illness Code', 'APR Severity of Illness Description',
       'APR Risk of Mortality', 'APR Medical Surgical Description',
       'Payment Typology 1', 'Payment Typology 2', 'Payment Typology 3',
       'Birth Weight', 'Abortion Edit Indicator',
       'Emergency Department Indicator', 'Total Charges', 'Total Costs'],
      dtype='object')

In [20]:
sparcs['Length of Stay'].describe()

count     23583
unique       97
top           2
freq       5378
Name: Length of Stay, dtype: object

In [21]:
sparcs['Total Costs'].describe()

count    2.358300e+04
mean     1.472282e+04
std      2.718098e+04
min      6.700000e-01
25%      4.471700e+03
50%      8.320120e+03
75%      1.590874e+04
max      1.591541e+06
Name: Total Costs, dtype: float64

In [22]:
sparcs['APR Risk of Mortality'].value_counts()

Minor       13990
Moderate     4952
Major        3452
Extreme      1187
Name: APR Risk of Mortality, dtype: int64

Developing a binary version of the sparcs data

In [23]:
sparcs['Length of Stay'] = pd.to_numeric(sparcs['Length of Stay'], errors='coerce')
sparcs['sparcs_los'] = sparcs['Length of Stay'].apply(lambda x: 'long' if x > 3 else 'short')
sparcs.drop('Length of Stay', axis=1, inplace=True)
sparcs['sparcs_los'].value_counts()

short    13008
long     10575
Name: sparcs_los, dtype: int64

In [24]:
X = sparcs.drop(columns=['sparcs_los'])
y = sparcs["sparcs_los"]

In [25]:
x

Health Service Area Hospital County  Operating Certificate Number  \
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
5              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23424         Long Island         Suffolk                     5155000.0   
23485         Long Island         Suffolk                     5157003.0   
23515         Long Island         Suffolk                     5157003.0   
23536         Long Island         Suffolk                     5157003.0   
23575         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
5             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23424        938.0                         Peconic Bay Medical Center   
23485        943.0                     St Catherine of Siena Hospital   
23515        943.0                     St Catherine of Siena Hospital   
23536        943.0                     St Catherine of Siena Hospital   
23575        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
5      70 or Older                 148      F       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23424  70 or Older                 119      F  Other Race  Not Span/Hispanic   
23485  70 or Older                 117      F       White  Not Span/Hispanic   
23515  70 or Older                 117      F       White  Not Span/Hispanic   
23536  70 or Older                 117      M       White  Not Span/Hispanic   
23575  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Severity of Illness Description  \
1      ...                               Minor   
2      ...                               Minor   
3      ...                            Moderate   
4      ...                             Extreme   
5      ...                            Moderate   
...    ...                                 ...   
23424  ...                               Minor   
23485  ...                               Minor   
23515  ...                            Moderate   
23536  ...                            Moderate   
23575  ...                            Moderate   

      APR Medical Surgical Description      Payment Typology 1  \
1                              Medical  Blue Cross/Blue Shield   
2                              Medical                Self-Pay   
3                              Medical                Medicare   
4                              Medical  Blue Cross/Blue Shield   
5                              Medical                Medicare   
...                                ...                     ...   
23424                          Medical                Medicare   
23485                         Surgical                Medicare   
23515                          Medical                Medicare   
23536 

In [26]:
y

0        short
1        short
2        short
3        short
4         long
         ...  
23578     long
23579    short
23580     long
23581     long
23582     long
Name: sparcs_los, Length: 23583, dtype: object

In [27]:
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, test_size=0.25)

In [28]:
automl = AutoML(
    results_path="sparcs_binary_los",
    mode="Explain"
)

In [29]:
automl.fit(X_train, y_train)

Linear algorithm was disabled.
AutoML directory: sparcs_binary_los
The task is binary_classification with evaluation metric logloss
AutoML will use algorithms: ['Baseline', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 2 models
1_Baseline logloss 0.687821 trained in 1.08 seconds


2_DecisionTree logloss 0.449524 trained in 21.75 seconds
* Step default_algorithms will try to check up to 3 models
3_Default_Xgboost logloss 0.254735 trained in 20.09 seconds
4_Default_NeuralNetwork logloss 0.358171 trained in 9.68 seconds
5_Default_RandomForest logloss 0.380731 trained in 12.61 seconds
* Step ensemble will try to check up to 1 model
Ensemble logloss 0.254735 trained in 1.57 seconds
AutoML fit time: 79.58 seconds
AutoML best model: 3_Default_Xgboost


AutoML(results_path='sparcs_binary_los')

In [30]:
pred = automl.predict(X_test)
pred

array(['short', 'short', 'long', ..., 'short', 'short', 'long'],
      dtype=object)

In [31]:
automl.report()

Testing new data

In [32]:
automl_sparcs_los = AutoML(results_path="sparcs_binary_los")

In [33]:
X_withlos = sparcs.sample(5)
X_withoutlos = X_withlos.drop(columns=['sparcs_los'])

In [34]:
predict = automl.predict(X_withoutlos)
predict

array(['long', 'long', 'long', 'short', 'long'], dtype=object)

In [35]:
values_actual = X_withlos['sparcs_los'].values.tolist()
values_predicted = predict.tolist()
output = pd.DataFrame({'actual': values_actual, 'predicted': values_predicted})
output

actual predicted
0   long      long
1   long      long
2   long      long
3  short     short
4   long      long

Binary Classifier Example

In [36]:
heart = pd.read_csv('https://raw.githubusercontent.com/csanicola74/AutoML-examples/main/data/heart.csv')
heart

age  sex  cp  trtbps  chol  fbs  restecg  thalachh  exng  oldpeak  slp  \
0     63    1   3     145   233    1        0       150     0      2.3    0   
1     37    1   2     130   250    0        1       187     0      3.5    0   
2     41    0   1     130   204    0        0       172     0      1.4    2   
3     56    1   1     120   236    0        1       178     0      0.8    2   
4     57    0   0     120   354    0        1       163     1      0.6    2   
..   ...  ...  ..     ...   ...  ...      ...       ...   ...      ...  ...   
298   57    0   0     140   241    0        1       123     1      0.2    1   
299   45    1   3     110   264    0        1       132     0      1.2    1   
300   68    1   0     144   193    1        1       141     0      3.4    1   
301   57    1   0     130   131    0        1       115     1      1.2    1   
302   57    0   1     130   236    0        0       174     0      0.0    1   

     caa  thall  output  
0      0      1       1  
1      0      2       1  
2      0      2       1  
3      0      2       1  
4      0      2       1  
..   ...    ...     ...  
298    0      3       0  
299    0      3       0  
300    2      3       0  
301    1      3       0  
302    1      2       0  

[303 rows x 14 columns]

In [37]:
heart.columns

Index(['age', 'sex', 'cp', 'trtbps', 'chol', 'fbs', 'restecg', 'thalachh',
       'exng', 'oldpeak', 'slp', 'caa', 'thall', 'output'],
      dtype='object')

In [38]:
heart['age'].describe()

count    303.000000
mean      54.366337
std        9.082101
min       29.000000
25%       47.500000
50%       55.000000
75%       61.000000
max       77.000000
Name: age, dtype: float64

In [39]:
heart['thalachh'].describe()

count    303.000000
mean     149.646865
std       22.905161
min       71.000000
25%      133.500000
50%      153.000000
75%      166.000000
max      202.000000
Name: thalachh, dtype: float64

In [40]:
heart['trtbps'].describe()

count    303.000000
mean     131.623762
std       17.538143
min       94.000000
25%      120.000000
50%      130.000000
75%      140.000000
max      200.000000
Name: trtbps, dtype: float64

In [41]:
heart['chol'].describe()

count    303.000000
mean     246.264026
std       51.830751
min      126.000000
25%      211.000000
50%      240.000000
75%      274.500000
max      564.000000
Name: chol, dtype: float64

In [42]:
X_without_chol = heart.drop(columns=['chol'])
y_chol = heart['chol']

In [43]:
X_without_chol

age  sex  cp  trtbps  fbs  restecg  thalachh  exng  oldpeak  slp  caa  \
0     63    1   3     145    1        0       150     0      2.3    0    0   
1     37    1   2     130    0        1       187     0      3.5    0    0   
2     41    0   1     130    0        0       172     0      1.4    2    0   
3     56    1   1     120    0        1       178     0      0.8    2    0   
4     57    0   0     120    0        1       163     1      0.6    2    0   
..   ...  ...  ..     ...  ...      ...       ...   ...      ...  ...  ...   
298   57    0   0     140    0        1       123     1      0.2    1    0   
299   45    1   3     110    0        1       132     0      1.2    1    0   
300   68    1   0     144    1        1       141     0      3.4    1    2   
301   57    1   0     130    0        1       115     1      1.2    1    1   
302   57    0   1     130    0        0       174     0      0.0    1    1   

     thall  output  
0        1       1  
1        2       1  
2        2       1  
3        2       1  
4        2       1  
..     ...     ...  
298      3       0  
299      3       0  
300      3       0  
301      3       0  
302      2       0  

[303 rows x 13 columns]

In [44]:
y_chol

0      233
1      250
2      204
3      236
4      354
      ... 
298    241
299    264
300    193
301    131
302    236
Name: chol, Length: 303, dtype: int64

In [45]:
automl_2 = AutoML()
automl_2.fit(X_without_chol,y_chol)

AutoML directory: AutoML_1
The task is regression with evaluation metric rmse
AutoML will use algorithms: ['Baseline', 'Linear', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 3 models
1_Baseline rmse 40.458838 trained in 1.16 seconds
2_DecisionTree rmse 46.646306 trained in 4.63 seconds
3_Linear rmse 40.094017 trained in 3.05 seconds
* Step default_algorithms will try to check up to 3 models
4_Default_Xgboost rmse 43.4703 trained in 3.22 seconds
5_Default_NeuralNetwork rmse 36.975542 trained in 1.47 seconds
6_Default_RandomForest rmse 37.908018 trained in 5.46 seconds
* Step ensemble will try to check up to 1 model
Ensemble rmse 36.759846 trained in 0.28 seconds
AutoML fit time: 27.57 seconds
AutoML best model: Ensemble


AutoML()

In [46]:
automl_2.report()

In [47]:
heart['reg_pred'] = automl_2.predict(X_without_chol)

In [48]:
print('reg_pred')
print(heart[['chol', 'reg_pred']].head())

reg_pred
   chol    reg_pred
0   233  242.030588
1   250  233.076180
2   204  256.958405
3   236  236.239116
4   354  253.012820


Porting files to a .zip

In [49]:
!zip -r /content/download.zip /content/

  adding: content/ (stored 0%)
  adding: content/.config/ (stored 0%)
  adding: content/.config/logs/ (stored 0%)
  adding: content/.config/logs/2022.12.06/ (stored 0%)
  adding: content/.config/logs/2022.12.06/14.34.52.796902.log (deflated 54%)
  adding: content/.config/logs/2022.12.06/14.33.25.230070.log (deflated 92%)
  adding: content/.config/logs/2022.12.06/14.34.25.129301.log (deflated 54%)
  adding: content/.config/logs/2022.12.06/14.34.16.877510.log (deflated 86%)
  adding: content/.config/logs/2022.12.06/14.33.49.923050.log (deflated 53%)
  adding: content/.config/logs/2022.12.06/14.34.53.595309.log (deflated 53%)
  adding: content/.config/.last_update_check.json (deflated 24%)
  adding: content/.config/gce (stored 0%)
  adding: content/.config/configurations/ (stored 0%)
  adding: content/.config/configurations/config_default (deflated 15%)
  adding: content/.config/.last_opt_in_prompt.yaml (stored 0%)
  adding: content/.config/.last_survey_prompt.yaml (stored 0%)
  adding: c

In [50]:
from google.colab import files
files.download('/content/download.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>